Copyright (c) Microsoft Corporation.

Licensed under the MIT License.

# Text2SQL with AutoGen & Azure OpenAI

This notebook demonstrates how the AutoGen Agents can be integrated with Azure OpenAI to answer questions from the database based on the schemas provided. 

A multi-shot approach is used for SQL generation for more reliable results and reduced token usage. More details can be found in the README.md.

### Dependencies

To install dependencies for this demo:

`uv sync --package autogen_text_2_sql`

`uv add --editable text_2_sql_core`

In [1]:
# This is only needed for this notebook to work
import sys
from pathlib import Path

# Add the parent directory of `src` to the path
sys.path.append(str(Path.cwd() / "src"))

In [2]:
import dotenv
import logging
from autogen_agentchat.ui import Console
from autogen_text_2_sql.autogen_text_2_sql import AutoGenText2Sql

In [3]:
logging.basicConfig(level=logging.INFO)

In [4]:
dotenv.load_dotenv()

True

## Bot setup

In [5]:
agentic_text_2_sql = AutoGenText2Sql(engine_specific_rules="", use_case="Analysing sales data across suppliers")

### Generated Queries

In [7]:
result = await agentic_text_2_sql.process_question(task="What total number of orders in June 2008?")
await Console(result)


INFO:root:Processing question: What total number of orders in June 2008?
INFO:root:Chat history: None
INFO:autogen_core:Sending message of type GroupChatStart to group_chat_manager: {'message': TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage')}
INFO:autogen_core:Calling message handler for group_chat_manager/6838d42b-6ed1-4ca6-bb46-12026e07f680 with message type GroupChatStart sent by Unknown
INFO:autogen_core:Publishing message of type GroupChatStart to all subscribers: {'message': TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage')}
INFO:autogen_core:Publishing message of type GroupChatStart to all subscribers: {'message': TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June

---------- user ----------
{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}


INFO:httpx:HTTP Request: POST https://aoai-text2sql-adi.openai.azure.com/openai/deployments/gpt-4o-mini/chat/completions?api-version=2024-08-01-preview "HTTP/1.1 200 OK"
INFO:autogen_core.events:{"prompt_tokens": 642, "completion_tokens": 15, "type": "LLMCall"}
/workspaces/dstoolkit-text2sql-and-imageprocessing/.venv/lib/python3.12/site-packages/autogen_agentchat/agents/_assistant_agent.py:307: UserWarning: Resolved model mismatch: gpt-4o-mini-2024-07-18 != gpt-4o-mini. Model mapping may be incorrect.
  result = await self._model_client.create(
INFO:autogen_core:Publishing message of type GroupChatMessage to all subscribers: {'message': TextMessage(source='query_rewrite_agent', models_usage=RequestUsage(prompt_tokens=642, completion_tokens=15), content='["What was the total number of orders in June 2008?"]', type='TextMessage')}
INFO:autogen_core:Publishing message of type GroupChatAgentResponse to all subscribers: {'agent_response': Response(chat_message=TextMessage(source='query_rewr

---------- query_rewrite_agent ----------
["What was the total number of orders in June 2008?"]
[Prompt tokens: 642, Completion tokens: 15]


INFO:root:Messages: [TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage'), TextMessage(source='query_rewrite_agent', models_usage=RequestUsage(prompt_tokens=642, completion_tokens=15), content='["What was the total number of orders in June 2008?"]', type='TextMessage')]
INFO:root:Decision: sql_query_cache_agent
INFO:autogen_core:Publishing message of type GroupChatRequestPublish to all subscribers: {}
INFO:autogen_core:Calling message handler for sql_query_cache_agent with message type GroupChatRequestPublish published by group_chat_manager/6838d42b-6ed1-4ca6-bb46-12026e07f680
INFO:root:Processing questions: ['What was the total number of orders in June 2008?']
INFO:root:Fetching queries from cache for question: What was the total number of orders in June 2008?
INFO:httpx:HTTP Request: POST https://aoai-text2sql-adi.openai.azure.com/openai/deployments/text-embe

...

INFO:root:Messages: [TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage'), TextMessage(source='query_rewrite_agent', models_usage=RequestUsage(prompt_tokens=642, completion_tokens=15), content='["What was the total number of orders in June 2008?"]', type='TextMessage'), TextMessage(source='sql_query_cache_agent', models_usage=None, content='{"cached_questions_and_schemas": [], "contains_pre_run_results": false}', type='TextMessage'), ToolCallMessage(source='sql_query_generation_agent', models_usage=RequestUsage(prompt_tokens=700, completion_tokens=25), content=[FunctionCall(id='call_JOtuS2RBtWICveApffPliwrg', arguments='{"text":"orders","excluded_entities":[],"as_json":true}', name='get_entity_schemas')], type='ToolCallMessage'), ToolCallResultMessage(source='sql_query_generation_agent', models_usage=None, content=[FunctionExecutionResult(content='[{"Columns": 

---------- sql_query_generation_agent ----------
I am currently unable to connect to the database server to execute the SQL query. Please check your database connection settings or firewall rules to ensure access. If you have any other questions or need further assistance, feel free to ask!
[Prompt tokens: 45702, Completion tokens: 46]


INFO:root:Messages: [TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage'), TextMessage(source='query_rewrite_agent', models_usage=RequestUsage(prompt_tokens=642, completion_tokens=15), content='["What was the total number of orders in June 2008?"]', type='TextMessage'), TextMessage(source='sql_query_cache_agent', models_usage=None, content='{"cached_questions_and_schemas": [], "contains_pre_run_results": false}', type='TextMessage'), ToolCallMessage(source='sql_query_generation_agent', models_usage=RequestUsage(prompt_tokens=700, completion_tokens=25), content=[FunctionCall(id='call_JOtuS2RBtWICveApffPliwrg', arguments='{"text":"orders","excluded_entities":[],"as_json":true}', name='get_entity_schemas')], type='ToolCallMessage'), ToolCallResultMessage(source='sql_query_generation_agent', models_usage=None, content=[FunctionExecutionResult(content='[{"Columns": 

---------- sql_query_correction_agent ----------
```json
{
  "error": "Unable to connect to the database server. Please check your database connection settings or firewall rules to ensure access."
}
```
[Prompt tokens: 45416, Completion tokens: 32]


INFO:root:Messages: [TextMessage(source='user', models_usage=None, content='{"user_question": "What total number of orders in June 2008?", "chat_history": {}, "parameters": null}', type='TextMessage'), TextMessage(source='query_rewrite_agent', models_usage=RequestUsage(prompt_tokens=642, completion_tokens=15), content='["What was the total number of orders in June 2008?"]', type='TextMessage'), TextMessage(source='sql_query_cache_agent', models_usage=None, content='{"cached_questions_and_schemas": [], "contains_pre_run_results": false}', type='TextMessage'), ToolCallMessage(source='sql_query_generation_agent', models_usage=RequestUsage(prompt_tokens=700, completion_tokens=25), content=[FunctionCall(id='call_JOtuS2RBtWICveApffPliwrg', arguments='{"text":"orders","excluded_entities":[],"as_json":true}', name='get_entity_schemas')], type='ToolCallMessage'), ToolCallResultMessage(source='sql_query_generation_agent', models_usage=None, content=[FunctionExecutionResult(content='[{"Columns": 